In [ ]:
def coc():
    dfc1=pd.DataFrame()
    headers = {'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/111.0.0.0 Safari/537.36'}
    req = requests.get("https://www.oyorooms.com/hotels-in-kochi/", headers=headers).text
    soup = Soup(req, 'html.parser')
    apts = soup.find_all("div", {"class": "oyo-row oyo-row--no-spacing listingHotelDescription"})
    l = []
    obj = {}
    for a in range(0, len(apts)):
        try:
            obj["pricing"] = apts[a].find("span", {"class": "listingPrice__finalPrice"}).text
        except: obj["pricing"] = None
        try:
            obj["address"] = apts[a].find("div", {"class": "d-body-lg listingHotelDescription__hotelAddress"}).text
        except:
            obj["address"] = None
        l.append(obj)
        obj = {}
    for i in l:
        price = i["pricing"]
        address = i["address"]
        dfc1 = dfc1.append({"price": price,"address": address}, ignore_index=True)
    dfc2=pd.DataFrame()
    for page in range(1,14):
        req1 = requests.get("https://www.booking.com/searchresults.en-us.html?ss=Cochin&ssne=Cochin&ssne_untouched=Cochin&label=gog235jc-1DCAMobEIGY29jaGluSDNYA2hsiAEBmAExuAEXyAEM2AED6AEB-AECiAIBqAIDuAKryf-hBsACAdICJGNmMmQ1ODhmLTJiYWYtNGQyNS05YzE5LWM2OWQyZjk4OTNmNdgCBOACAQ&sid=98568152db64b2f303d5bb990da98b4c&aid=356980&lang=en-us&sb=1&src_elem=sb&src=searchresults&dest_id=-2093645&dest_type=city&checkin=2023-05-01&checkout=2023-05-02&group_adults=2&no_rooms=1&group_children=0&sb_travel_purpose=leisure/{}_p/".format(page),headers=headers).text
        soup = Soup(req1, 'html.parser')
        apts = soup.find_all("div", {"class": "a1b3f50dcd a1f3ecff04 f7c6687c3d f996d8c258"})
        l = []
        obj = {}
        for a in range(0, len(apts)):
            try:
                obj["pricing"] = apts[a].find("span", {"class": "fcab3ed991 fbd1d3018c e729ed5ab6"}).text
            except: obj["pricing"] = None
            try:
                obj["address"] = apts[a].find("span", {"class": "f4bd0794db b4273d69aa"}).text
            except:
                obj["address"] = None
            l.append(obj)
            obj = {}
        for i in l:
            price = i["pricing"]
            address = i["address"]
            dfc2 = dfc2.append({"price": price,"address": address}, ignore_index=True)
    df = pd.concat([dfc1, dfc2], ignore_index=True)
    df["price"] = df["price"].str.replace(r"₹", "")
    df["price"] = df["price"].str.replace(r",", "")
    df['price'] = df['price'].astype(float)
    return df
coc()

In [ ]:
#added more features
import requests 
from bs4 import BeautifulSoup as Soup
import pandas as pd
def delhi():
    df=pd.DataFrame()
    headers = {'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/112.0.0.0 Safari/537.36'}
    for page in range (1,6):
        req = requests.get("https://www.oyorooms.com/hotels-in-delhi/{}_p/".format(page), headers=headers).text
        soup = Soup(req, 'html.parser')
        print(soup)
        apts = soup.find_all("div", {"class": "oyo-row oyo-row--no-spacing listingHotelDescription"})
        print(apts)
        l = []
        obj = {}
        apts1 = soup.find_all(itemprop='url')
        for a in range(0, len(apts)):
            try:
                obj["pricing"] = apts[a].find("span", {"class": "listingPrice__finalPrice"}).text
            except: obj["pricing"] = None
            try:
                obj["Distance"] = apts[a].find("span", {"class": "listingHotelDescription__distanceText"}).text
            except:
                obj["Distance"] = None
            try:
                link= apts1[a].get('content')
                req1 = requests.get(link, headers=headers).text
                soup2 = Soup(req1, 'html.parser')
                obj["amneties"] = soup2.find("div", {"class": "c-2cojj"}).text
            except:
                obj["amneties"] = None
            try:
                obj["ratings"] = apts[a].find("div", {"class": "hotelRating"}).text
            except:
                obj["ratings"] = None
            
            l.append(obj)
            obj = {}
        for i in l:
            price = i["pricing"]
            distance = i["Distance"]
            amneties= i["amneties"]
            ratings= i["ratings"]
            df = df.append({"price": price,"distance": distance,"amneties":amneties,"ratings":ratings}, ignore_index=True)
    print(df)
#dataCleaning
    df["price"] = df["price"].str.replace(r"₹", "")
    df["ratings"] = df["ratings"].str.replace(r"₹", "")
    df['price'] = pd.to_numeric(df['price'])
    df['distance']=df['distance'].str.replace(r"km","")
    df['distance'] = pd.to_numeric(df['distance'])
    df[['ratings', 'last_name','y','x']] = df['ratings'].str.split(' ', expand=True)
    df = df.drop(columns=['last_name','y','x'],axis=1)
    df['ratings'] = pd.to_numeric(df['ratings'],errors='coerce')
    import re
    df['wifi'] = df['amneties'].str.extract(r'(Wifi)', expand=False,flags=re.IGNORECASE)
    df['AC'] = df['amneties'].str.extract(r'(AC)', expand=False)
    df['amneties']=df['amneties'].str.replace(r"CCTV","")
    df['TV'] = df['amneties'].str.extract(r'(TV)', expand=False)
    df['Queen Sized Bed'] = df['amneties'].str.extract(r'(Queen Sized Bed)', expand=False)
    df['Geyser'] = df['amneties'].str.extract(r'(Geyser)', expand=False)
    df['King Sized Bed'] = df['amneties'].str.extract(r'(King Sized Bed)', expand=False)
    df['Power backup'] = df['amneties'].str.extract(r'(Power backup)', expand=False)
    df['Mini Fridge'] = df['amneties'].str.extract(r'(Mini Fridge)', expand=False)
    df= df.drop(columns=['amneties'],axis= 1)
    df['AC'] = df['AC'].fillna('').replace({'': 0, '[^0]': 1}, regex=True)
    df['TV'] = df['TV'].fillna('').replace({'': 0, '[^0]': 1}, regex=True)
    df['wifi'] = df['wifi'].fillna('').replace({'': 0, '[^0]': 1}, regex=True)
    df['Queen Sized Bed'] = df['Queen Sized Bed'].fillna('').replace({'': 0, '[^0]': 1}, regex=True)
    df['King Sized Bed'] = df['King Sized Bed'].fillna('').replace({'': 0, '[^0]': 1}, regex=True)
    df['Geyser'] = df['Geyser'].fillna('').replace({'': 0, '[^0]': 1}, regex=True)
    df['Power backup'] = df['Power backup'].fillna('').replace({'': 0, '[^0]': 1}, regex=True)
    df['Mini Fridge'] = df['Mini Fridge'].fillna('').replace({'': 0, '[^0]': 1}, regex=True)
    df['Mini Fridge'] = df['Mini Fridge'].fillna('').replace({'': 0, '[^0]': 1}, regex=True)
    df['ratings'] = df['ratings'].fillna(df['ratings'].mean())
    return df
df= delhi()
df

In [ ]:
import requests 
from bs4 import BeautifulSoup as Soup
import pandas as pd
def delhi():
    df=pd.DataFrame()
    headers = {'User-Agent': 'User-Agent: Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/111.0.0.0 Safari/537.36'}
    req = requests.get("https://www.oyorooms.com/hotels-in-delhi/", headers=headers).text
    soup = Soup(req.text, 'html.parser')
    apts = soup.find_all("div", {"class": "oyo-row oyo-row--no-spacing listingHotelDescription"})
    l = []
    obj = {}
    apts1 = soup.find_all(itemprop='url')
    for a in range(0, len(apts)):
        try:
            obj["pricing"] = apts[a].find("span", {"class": "listingPrice__finalPrice"}).text
        except: obj["pricing"] = None
        try:
            obj["Distance"] = apts[a].find("span", {"class": "listingHotelDescription__distanceText"}).text
        except:
            obj["Distance"] = None
        try:
            link= apts1[a].get('content')
            req1 = requests.get(link, headers=headers).text
            soup2 = Soup(req1, 'html.parser')
            obj["amneties"] = soup2.find("div", {"class": "c-2cojj"}).text
        except:
            obj["amneties"] = None
        try:
            obj["ratings"] = apts[a].find("div", {"class": "hotelRating"}).text
        except:
            obj["ratings"] = None
            
        l.append(obj)
        obj = {}
    for i in l:
        price = i["pricing"]
        distance = i["Distance"]
        amneties= i["amneties"]
        ratings= i["ratings"]
        df = df.append({"price": price,"distance": distance,"amneties":amneties,"ratings":ratings}, ignore_index=True)
    df["price"] = df["price"].str.replace(r"₹", "")
    df["ratings"] = df["ratings"].str.replace(r"₹", "")
    df['price'] = pd.to_numeric(df['price'])
    df['distance']=df['distance'].str.replace(r"km","")
    df['distance'] = pd.to_numeric(df['distance'])
    df[['ratings', 'last_name','y','x']] = df['ratings'].str.split(' ', expand=True)
    df = df.drop(columns=['last_name','y','x'],axis=1)
    df['ratings'] = pd.to_numeric(df['ratings'],errors='coerce')
    dfg['AC'] = dfg['AC'].fillna('').replace({'': 0, '[^0]': 1}, regex=True)
    dfg['TV'] = dfg['TV'].fillna('').replace({'': 0, '[^0]': 1}, regex=True)
    dfg['wifi'] = dfg['wifi'].fillna('').replace({'': 0, '[^0]': 1}, regex=True)
    dfg['Queen Sized Bed'] = dfg['Queen Sized Bed'].fillna('').replace({'': 0, '[^0]': 1}, regex=True)
    dfg['King Sized Bed'] = dfg['King Sized Bed'].fillna('').replace({'': 0, '[^0]': 1}, regex=True)
    dfg['Geyser'] = dfg['Geyser'].fillna('').replace({'': 0, '[^0]': 1}, regex=True)
    dfg['Power backup'] = dfg['Power backup'].fillna('').replace({'': 0, '[^0]': 1}, regex=True)
    dfg['Mini Fridge'] = dfg['Mini Fridge'].fillna('').replace({'': 0, '[^0]': 1}, regex=True)
    dfg['Mini Fridge'] = dfg['Mini Fridge'].fillna('').replace({'': 0, '[^0]': 1}, regex=True)
    import numpy as np
    dfg['ratings'] = df['ratings'].replace({'NEW': np.nan})
    df['ratings'] = pd.to_numeric(df['ratings'],errors='coerce')
    dfg['ratings'] = dfg['ratings'].fillna(df['ratings'].mean())
    dfg

    return df
dfd= delhi()

In [ ]:
import pandas as pd
df= pd.read_csv('delhiclean.csv')
df = df.drop(columns=['wifi','AC','TV'],axis=1)
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
x = df.iloc[:,:1]
y = df.iloc[:,1:3]
x_train, x_test, y_train, y_test = train_test_split(x,y, test_size = 0.2, random_state = 10)
lnr = LinearRegression().fit(x_train, y_train)
y_pred = lnr.predict(x_test)
from sklearn.metrics import r2_score
r2 = r2_score(y_test, y_pred)
r2





In [ ]:
import requests 
from bs4 import BeautifulSoup as Soup
import pandas as pd
df=pd.read_csv('delhiclean.csv')
print(df.head())
import matplotlib.pyplot as plt
from sklearn.model_selection import ShuffleSplit, train_test_split
from sklearn.metrics import mean_squared_log_error as msle, mean_squared_error as mse, mean_absolute_error as mae
train, test = train_test_split(df, test_size=1/14, random_state=42)
train, valid = train_test_split(train, test_size=1/13, random_state=42)
print('Train shape:', train.shape)
print('Validation shape:', valid.shape)
print('Test shape:', test.shape)
train['price'].hist(bins=100)
plt.title('Price Histogram in Train Split')
#plt.xlim(0,300)
plt.xlabel('Price')
plt.ylabel('Count')
plt.show()


In [ ]:
from sklearn.preprocessing import PowerTransformer

pt = PowerTransformer(method='box-cox')
y_train = pt.fit_transform(train['price'].values.reshape(-1,1))
pd.Series(y_train.ravel()).hist()
plt.title('Price Histogram in Train Split')
plt.xlabel('Transformed Price')
plt.ylabel('Count')
plt.show()

In [ ]:
from pycaret.regression import *
from operator import itemgetter
from sklearn.feature_extraction import DictVectorizer
from preprocess import preprocess
from sklearn.feature_extraction.text import TfidfVectorizer as Tfidf
from sklearn.pipeline import make_pipeline, make_union
from sklearn.preprocessing import FunctionTransformer
def preprocess(df, include_target=False):
    if include_target:
        return df[['price','distance','ratings','wifi','AC','TV','Queen Sized Bed','Geyser']]
    else:
        return df[['distance','ratings','wifi','AC','TV','Queen Sized Bed','Geyser']]
def on_field(f, *vec):
    return make_pipeline(FunctionTransformer(itemgetter(f), validate=False), *vec)

def to_records(df):
    return df.to_dict(orient='records')

def make_vec(max_features=None):
    vectorizer = make_union(
        on_field('name', Tfidf(max_features=max_features, token_pattern='\w+')),
        on_field('text', Tfidf(max_features=max_features, token_pattern='\w+', ngram_range=(1, 2))),
        on_field(['shipping', 'condition'],
                 FunctionTransformer(to_records, validate=False), DictVectorizer()),
        n_jobs=-1
    )
    return vectorizer


RS=42
data = preprocess(df, include_target=True)

vectorizer = make_vec(10000)

exp_partial = setup(
    data=data.sample(int(0.1*len(data)), random_state=RS), 
    target='price',
    train_size=13/14,
    preprocess=True,
    transform_target=True,
    fold_strategy=ShuffleSplit(1, train_size=12/13, random_state=RS),
    use_gpu=True,
    custom_pipeline=vectorizer,
    session_id=RS,
    log_experiment=True,
    experiment_name='price_recom_partial',
)
compare_models(include=['lr', 'lasso', 'ridge', 'en', 'huber', 'knn', 'ada', 'gbr']);



In [ ]:
from pycaret.regression import *
import pandas as pd
data = pd.read_csv('delhiclean.csv')

regression_setup = setup(
    data,
    target='price',
    normalize=True,
    train_size=0.8,
    session_id=123,
    log_experiment=True,
    experiment_name='your_experiment_name'
)

best_models = compare_models(
    fold=5, 
    sort='RMSLE', 
    n_select=3, 
    exclude=['catboost'], 
    turbo=True
)

print(best_models)







In [ ]:
from pycaret.regression import *
import pandas as pd
data = pd.read_csv('delhiclean.csv')

regression_setup = setup(
    data,
    target='price',
    normalize=True,
    train_size=0.8,
    session_id=123,
    log_experiment=True,
    experiment_name='your_experiment_name'
)

best_models = compare_models()

print(best_models)

In [ ]:
X_train = vectorizer.fit_transform(preprocess(train)).astype(np.float32)
X_valid = vectorizer.transform(preprocess(valid)).astype(np.float32)
print(f'X_train: {X_train.shape} of {X_train.dtype}')
print(f'X_valid: {X_valid.shape} of {X_valid.dtype}')

In [ ]:
import requests 
from bs4 import BeautifulSoup as Soup
import pandas as pd
def delhi1():
    df=pd.DataFrame()
    headers = {'User-Agent': 'User-Agent: Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/111.0.0.0 Safari/537.36'}
    req = requests.get("https://www.oyorooms.com/hotels-in-delhi/", headers=headers).text
    soup = Soup(req, 'html.parser')
    apts = soup.find_all("div", {"class": "oyo-row oyo-row--no-spacing listingHotelDescription"})
    l = []
    obj = {}
    apts1 = soup.find_all(itemprop='url')
    for a in range(0, len(apts)):
        try:
            obj["pricing"] = apts[a].find("span", {"class": "listingPrice__finalPrice"}).text
        except: obj["pricing"] = None
        try:
            obj["Distance"] = apts[a].find("span", {"class": "listingHotelDescription__distanceText"}).text
        except:
            obj["Distance"] = None
        try:
            link= apts1[a].get('content')
            req1 = requests.get(link, headers=headers).text
            soup2 = Soup(req1, 'html.parser')
            obj["amneties"] = soup2.find("div", {"class": "c-2cojj"}).text
        except:
            obj["amneties"] = None
        try:
            obj["ratings"] = apts[a].find("div", {"class": "hotelRating"}).text
        except:
            obj["ratings"] = None
            
        l.append(obj)
        obj = {}
    for i in l:
        price = i["pricing"]
        distance = i["Distance"]
        amneties= i["amneties"]
        ratings= i["ratings"]
        df = df.append({"price": price,"distance": distance,"amneties":amneties,"ratings":ratings}, ignore_index=True)
    df["price"] = df["price"].str.replace(r"₹", "")
    df["ratings"] = df["ratings"].str.replace(r"₹", "")
    df['price'] = pd.to_numeric(df['price'])
    df['distance']=df['distance'].str.replace(r"km","")
    df['distance'] = pd.to_numeric(df['distance'])
    df[['ratings', 'last_name','y','x']] = df['ratings'].str.split(' ', expand=True)
    df = df.drop(columns=['last_name','y','x'],axis=1)
    df['ratings'] = pd.to_numeric(df['ratings'],errors='coerce')
    return df


In [ ]:
df= delhi1()

In [ ]:

df

    


In [ ]:
df['ratings'] = df['ratings'].fillna(df['ratings'].mean())
df.to_csv('newdata.csv', index=False)



In [ ]:
df=pd.read_csv('newdata.csv')
df

In [ ]:
import requests 
from bs4 import BeautifulSoup as Soup
import pandas as pd
df=pd.read_csv('newdata.csv')
print(df.head())
import matplotlib.pyplot as plt
from sklearn.model_selection import ShuffleSplit, train_test_split
from sklearn.metrics import mean_squared_log_error as msle, mean_squared_error as mse, mean_absolute_error as mae
train, test = train_test_split(df, test_size=1/14, random_state=42)
train, valid = train_test_split(train, test_size=1/13, random_state=42)
print('Train shape:', train.shape)
print('Validation shape:', valid.shape)
print('Test shape:', test.shape)
train['price'].hist(bins=100)
plt.title('Price Histogram in Train Split')
#plt.xlim(0,300)
plt.xlabel('Price')
plt.ylabel('Count')
plt.show()
from sklearn.preprocessing import PowerTransformer
pt = PowerTransformer(method='box-cox')
y_train = pt.fit_transform(train['price'].values.reshape(-1,1))
pd.Series(y_train.ravel()).hist()
plt.title('Price Histogram in Train Split')
plt.xlabel('Transformed Price')
plt.ylabel('Count')
plt.show()

In [ ]:
from pycaret.regression import *
from sklearn.model_selection import ShuffleSplit, train_test_split
import pandas as pd
from operator import itemgetter
from sklearn.feature_extraction import DictVectorizer
from preprocess import preprocess
from sklearn.feature_extraction.text import TfidfVectorizer as Tfidf
from sklearn.pipeline import make_pipeline, make_union
from sklearn.preprocessing import FunctionTransformer
df=pd.read_csv('newdata.csv')

def preprocess(df, include_target=False):
    if include_target:
        return df[['price','distance','amneties','ratings']]
    else:
        return df[['distance','amneties','ratings']]
def on_field(f, *vec):
    return make_pipeline(FunctionTransformer(itemgetter(f), validate=False), *vec)

def to_records(df):
    return df.to_dict(orient='records')

def make_vec(max_features=None):
    vectorizer = make_union(
        #on_field('name', Tfidf(max_features=max_features, token_pattern='\w+')),
        on_field('amneties', Tfidf(max_features=max_features, token_pattern='\w+', ngram_range=(1, 2))),
        on_field(['ratings','distance'],
                 FunctionTransformer(to_records, validate=False), DictVectorizer()),
        n_jobs=1
    )
    return vectorizer


RS=42
data = preprocess(df, include_target=True)

vectorizer = make_vec(10000)

exp_partial = setup(
    data_func=lambda: data.sample(int(0.5*len(data)), random_state=RS),
    target='price',
    train_size=13/14,
    preprocess=False,
    transform_target=True,
    fold_strategy=ShuffleSplit(1, train_size=12/13, random_state=RS),
    use_gpu=True,
    custom_pipeline=vectorizer,
    session_id=RS,
    log_experiment=True,
    experiment_name='price_recomm_partial',
)





In [ ]:
best_models = compare_models()

print(best_models)

In [3]:
import requests 
from bs4 import BeautifulSoup as Soup
import pandas as pd
def delhi():
    df=pd.DataFrame()
    
    headers = {'User-Agent': 'User-Agent: Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/111.0.0.0 Safari/537.36'}
    for page in range (1,6):
        req = requests.get("https://www.oyorooms.com/hotels-in-delhi/?page={}".format(page), headers=headers).text
        soup = Soup(req, 'html.parser')
        apts = soup.find_all("div", {"class": "oyo-row oyo-row--no-spacing listingHotelDescription"})
        l = []
        obj = {}
        apts1 = soup.find_all(itemprop='url')
        for a in range(0, len(apts)):
            try:
                obj["pricing"] = apts[a].find("span", {"class": "listingPrice__finalPrice"}).text
            except: obj["pricing"] = None
            try:
                obj["Distance"] = apts[a].find("span", {"class": "listingHotelDescription__distanceText"}).text
            except:
                obj["Distance"] = None
            try:
                link= apts1[a].get('content')
                req1 = requests.get(link, headers=headers).text
                soup2 = Soup(req1, 'html.parser')
                obj["amneties"] = soup2.find("div", {"class": "c-2cojj"}).text
            except:
                obj["amneties"] = None
            try:
                obj["ratings"] = apts[a].find("div", {"class": "hotelRating"}).text
            except:
                obj["ratings"] = None
            
            l.append(obj)
            obj = {}
        for i in l:
            price = i["pricing"]
            distance = i["Distance"]
            amneties= i["amneties"]
            ratings= i["ratings"]
            df = df.append({"price": price,"distance": distance,"amneties":amneties,"ratings":ratings}, ignore_index=True)
#dataCleaning
    df["price"] = df["price"].str.replace(r"₹", "")
    df["ratings"] = df["ratings"].str.replace(r"₹", "")
    df['price'] = pd.to_numeric(df['price'])
    df['distance']=df['distance'].str.replace(r"km","")
    df['distance'] = pd.to_numeric(df['distance'])
    df[['ratings', 'last_name','y','x']] = df['ratings'].str.split(' ', expand=True)
    df = df.drop(columns=['last_name','y','x'],axis=1)
    df['ratings'] = pd.to_numeric(df['ratings'],errors='coerce')

In [4]:
df=delhi()
df

C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3233571860.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price,"distance": distance,"amneties":amneties,"ratings":ratings}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3233571860.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price,"distance": distance,"amneties":amneties,"ratings":ratings}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3233571860.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price,"distance": distance,"amneties":amneties,"ratings":ratings}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3233

C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3233571860.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price,"distance": distance,"amneties":amneties,"ratings":ratings}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3233571860.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price,"distance": distance,"amneties":amneties,"ratings":ratings}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3233571860.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price,"distance": distance,"amneties":amneties,"ratings":ratings}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3233

C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3233571860.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price,"distance": distance,"amneties":amneties,"ratings":ratings}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3233571860.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price,"distance": distance,"amneties":amneties,"ratings":ratings}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3233571860.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price,"distance": distance,"amneties":amneties,"ratings":ratings}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3233

In [5]:
df

In [43]:
# Web Scrapping OYO Working Code
import requests
from bs4 import BeautifulSoup as Soup
import pandas as pd
def delhi():
    df = pd.DataFrame()
    headers = {
        'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/111.0.0.0 Safari/537.36'}
    for pages in range(1, 6):
        req = requests.get(
            f"https://www.oyorooms.com/hotels-in-delhi/?page={pages}", headers=headers).text
        soup = Soup(req, 'html.parser')
        apts = soup.find_all(
            "div", {"class": "oyo-row oyo-row--no-spacing listingHotelDescription"})
        l = []
        obj = {}
        apts1 = soup.find_all(itemprop='url')
        for a in range(0, len(apts)):
            try:
                obj["pricing"] = apts[a].find(
                    "span", {"class": "listingPrice__finalPrice"}).text
            except:
                obj["pricing"] = None
            try:
                obj["Distance"] = apts[a].find(
                    "span", {"class": "listingHotelDescription__distanceText"}).text
            except:
                obj["Distance"] = None
            try:
                link = apts1[a].get('content')
                req1 = requests.get(link, headers=headers).text
                soup2 = Soup(req1, 'html.parser')
                ap=soup2.find_all("div", {"class": "c-riklip"})
                stri=''
                for b in range(0,len(ap)):
                    if "striked" not in ap[b].get("class", []):
                        stri += ap[b].find("div", {"class": "c-12w6zty"}).text + " "
                obj["amneties"] = stri.strip()
            except:
                obj["amneties"] = None
            try:
                obj["ratings"] = apts[a].find(
                    "div", {"class": "hotelRating"}).text
            except:
                obj["ratings"] = None

            l.append(obj)
            obj = {}
        for i in l:
            price = i["pricing"]
            distance = i["Distance"]
            amneties = i["amneties"]
            ratings = i["ratings"]
            df = df.append({"price": price, "distance": distance,
                           "amneties": amneties, "ratings": ratings}, ignore_index=True)
# dataCleaning
    df["price"] = df["price"].str.replace(r"₹", "")
    df["ratings"] = df["ratings"].str.replace(r"₹", "")
    df['price'] = pd.to_numeric(df['price'])
    df['distance'] = df['distance'].str.replace(r"km", "")
    df['distance'] = pd.to_numeric(df['distance'])
    df[['ratings', 'last_name', 'y', 'x']
       ] = df['ratings'].str.split(' ', expand=True)
    df = df.drop(columns=['last_name', 'y', 'x'], axis=1)
    df['ratings'] = pd.to_numeric(df['ratings'], errors='coerce')
    df['ratings'] = df['ratings'].fillna(df['ratings'].mean())
    return df
df = delhi()
df['price'] = df['price'].fillna(df['price'].mean())
df.to_csv('test1.csv')

C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3389623542.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "distance": distance,
C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3389623542.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "distance": distance,
C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3389623542.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "distance": distance,
C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3389623542.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price

C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3389623542.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "distance": distance,
C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3389623542.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "distance": distance,
C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3389623542.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "distance": distance,
C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3389623542.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price

C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3389623542.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "distance": distance,
C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3389623542.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "distance": distance,
C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3389623542.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "distance": distance,
C:\Users\Hashif\AppData\Local\Temp\ipykernel_24656\3389623542.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price

In [44]:
dft=pd.read_csv('test1.csv')
dft

Unnamed: 0        price  distance  \
0            0  1199.000000       5.1   
1            1   799.000000       5.0   
2            2   747.000000       4.0   
3            3   576.000000       8.8   
4            4   699.000000       1.7   
..         ...          ...       ...   
95          95  1153.977778       5.1   
96          96  1153.977778       8.2   
97          97  1153.977778       5.7   
98          98  1153.977778       1.6   
99          99  1153.977778       3.1   

                                             amneties  ratings  
0   AC TV Free Wifi Mini Fridge Seating area Power...  4.60000  
1   AC Free Wifi Queen Sized Bed TV Power backup G...  4.00000  
2        AC Free Wifi TV Geyser Power backup Elevator  3.36129  
3                   AC Kitchen TV Geyser Power backup  3.10000  
4        AC Free Wifi TV Power backup Geyser Elevator  2.30000  
..                                                ...      ...  
95                AC Free Wifi TV Geyser Power backup  4.70000  
96            AC Free Wifi Kitchen TV Geyser Elevator  4.10000  
97  Complimentary Buffet Breakfast AC TV Free Wifi...  4.30000  
98                AC Free Wifi TV Geyser Power backup  2.00000  
99       AC Free Wifi TV Geyser Power backup Elevator  3.40000  

[100 rows x 5 columns]

In [2]:
import requests
from bs4 import BeautifulSoup as Soup
import pandas as pd
df = pd.DataFrame()
headers = {'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/113.0.0.0 Safari/537.36'}
for pages in range(0, 39):
    req = requests.get(f"https://www.booking.com/searchresults.en-gb.html?label=gog235jc-1FCAIobDgOSAlYA2hsiAEBmAEJuAEXyAEM2AEB6AEB-AECiAIBqAIDuAKw3J2jBsACAdICJDNlOWY5MDE2LWRkNzMtNDBhZS1iMjQ2LTQ5ZTk2ZDJmYjU5ZdgCBeACAQ&sid=78a835dba3d7708eeae1b91933ba50ae&aid=356980&checkin=2023-06-01&checkout=2023-06-02&dest_id=-2106102&dest_type=city&srpvid=c0886213ab84013a&track_hp_back_button=1&offset={pages*25}", headers=headers).text
    soup = Soup(req, 'html.parser')
    apts = soup.find_all("div", {"class": "d20f4628d0"})
    l = []
    obj = {}
    for a in range(0, len(apts)):
        try:
            obj["pricing"] = apts[a].find("span", {"class": "fcab3ed991 fbd1d3018c e729ed5ab6"}).text
        except:
            obj["pricing"] = None
        try:
            obj["Distance"] = apts[a].find("span", {"class": "cb5ebe3ffb"}).text
        except:
            obj["Distance"] = None
        try:
            ap1=apts[a].find('a',href=True)
            link = ap1['href']
            req1 = requests.get(link, headers=headers).text
            soup2 = Soup(req1, 'html.parser')
            obj["amenities"] = soup2.find("div", {"class": "e5e0727360"}).text
        except:
            obj["amenities"] = None
        try:
            obj["ratings"] = apts[a].find("div", {"class": "b5cd09854e d10a6220b4"}).text
        except:
            obj["ratings"] = None
        try:
            obj["type"] = apts[a].find("span", {"class": "df597226dd"}).text
        except:
            obj["type"] = None
        try:
            obj["location"] = apts[a].find("span", {"class": "f4bd0794db b4273d69aa"}).text
        except:
            obj["location"] = None
    
    
        l.append(obj)
        obj = {}
        for i in l:
            price = i["pricing"]
            distance = i["Distance"]
            amenities = i["amenities"]
            ratings = i["ratings"]
            room_type=i["type"]
            location=i["location"]
            df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
# dataCleaning
df["price"] = df["price"].str.replace(r"₹", "")
df["price"] = df["price"].str.replace(r" ", "")
df["price"] = df["price"].str.replace(r",", "")
df["price"] = df["price"].str.strip() 
df['price'] = pd.to_numeric(df['price'])
df['ratings'] = pd.to_numeric(df['ratings'], errors='coerce')
df['ratings'] = df['ratings'].fillna(df['ratings'].mean())
dfd=dfd.drop_duplicates(ignore_index=True)
df.to_csv('test.csv')
df   

C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities

C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities

C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities

C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities

C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities

...

C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities

C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities

C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities

C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities": amenities, "ratings": ratings,"type":room_type}, ignore_index=True)
C:\Users\Hashif\AppData\Local\Temp\ipykernel_12272\325393101.py:52: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({"price": price, "location":location,"distance": distance,"amenities

price                 location distance  \
0        900  Pashim Vihar, New Delhi            
1        900  Pashim Vihar, New Delhi            
2       4125     Paharganj, New Delhi            
3        900  Pashim Vihar, New Delhi            
4       4125     Paharganj, New Delhi            
...      ...                      ...      ...   
12670    542    Mahipalpur, New Delhi            
12671    745        Rohini, New Delhi            
12672    739    West Delhi, New Delhi            
12673    553                New Delhi            
12674   1274    South West, New Delhi            

                                               amenities  ratings  \
0      Room service Non-smoking rooms Free WiFi Free ...      8.5   
1      Room service Non-smoking rooms Free WiFi Free ...      8.5   
2      Airport shuttle Room service Fitness centre No...      8.3   
3      Room service Non-smoking rooms Free WiFi Free ...      8.5   
4      Airport shuttle Room service Fitness centre No...      8.3   
...                                                  ...      ...   
12670  Room service Free WiFi 24-hour front desk Dail...      1.0   
12671  Room service Family rooms 24-hour front desk D...      8.0   
12672                                  Air conditioning       6.0   
12673                                  Air conditioning       2.0   
12674  Airport shuttle Room service Non-smoking rooms...      4.0   

                                          type  
0      Deluxe Double Room (2 Adults + 1 Child)  
1      Deluxe Double Room (2 Adults + 1 Child)  
2                 Superior Double or Twin Room  
3      Deluxe Double Room (2 Adults + 1 Child)  
4                 Superior Double or Twin Room  
...                                        ...  
12670                       Deluxe Triple Room  
12671                      Classic Triple Room  
12672                     Standard Double Room  
12673                      Classic Triple Room  
12674                     Standard Double Room  

[12675 rows x 6 columns]

In [25]:
import pandas as pd
dfd=pd.read_csv('test.csv')

In [16]:
dfd

Unnamed: 0  price                 location  distance  \
0               0    900  Pashim Vihar, New Delhi       NaN   
1               1    900  Pashim Vihar, New Delhi       NaN   
2               2   4125     Paharganj, New Delhi       NaN   
3               3    900  Pashim Vihar, New Delhi       NaN   
4               4   4125     Paharganj, New Delhi       NaN   
...           ...    ...                      ...       ...   
12670       12670    542    Mahipalpur, New Delhi       NaN   
12671       12671    745        Rohini, New Delhi       NaN   
12672       12672    739    West Delhi, New Delhi       NaN   
12673       12673    553                New Delhi       NaN   
12674       12674   1274    South West, New Delhi       NaN   

                                               amenities  ratings  \
0      Room service Non-smoking rooms Free WiFi Free ...      8.5   
1      Room service Non-smoking rooms Free WiFi Free ...      8.5   
2      Airport shuttle Room service Fitness centre No...      8.3   
3      Room service Non-smoking rooms Free WiFi Free ...      8.5   
4      Airport shuttle Room service Fitness centre No...      8.3   
...                                                  ...      ...   
12670  Room service Free WiFi 24-hour front desk Dail...      1.0   
12671  Room service Family rooms 24-hour front desk D...      8.0   
12672                                  Air conditioning       6.0   
12673                                  Air conditioning       2.0   
12674  Airport shuttle Room service Non-smoking rooms...      4.0   

                                          type  
0      Deluxe Double Room (2 Adults + 1 Child)  
1      Deluxe Double Room (2 Adults + 1 Child)  
2                 Superior Double or Twin Room  
3      Deluxe Double Room (2 Adults + 1 Child)  
4                 Superior Double or Twin Room  
...                                        ...  
12670                       Deluxe Triple Room  
12671                      Classic Triple Room  
12672                     Standard Double Room  
12673                      Classic Triple Room  
12674                     Standard Double Room  

[12675 rows x 7 columns]

In [26]:
dfd=dfd.drop(['Unnamed: 0'],axis=1)


In [18]:
dfd

price                 location  distance  \
0        900  Pashim Vihar, New Delhi       NaN   
1        900  Pashim Vihar, New Delhi       NaN   
2       4125     Paharganj, New Delhi       NaN   
3        900  Pashim Vihar, New Delhi       NaN   
4       4125     Paharganj, New Delhi       NaN   
...      ...                      ...       ...   
12670    542    Mahipalpur, New Delhi       NaN   
12671    745        Rohini, New Delhi       NaN   
12672    739    West Delhi, New Delhi       NaN   
12673    553                New Delhi       NaN   
12674   1274    South West, New Delhi       NaN   

                                               amenities  ratings  \
0      Room service Non-smoking rooms Free WiFi Free ...      8.5   
1      Room service Non-smoking rooms Free WiFi Free ...      8.5   
2      Airport shuttle Room service Fitness centre No...      8.3   
3      Room service Non-smoking rooms Free WiFi Free ...      8.5   
4      Airport shuttle Room service Fitness centre No...      8.3   
...                                                  ...      ...   
12670  Room service Free WiFi 24-hour front desk Dail...      1.0   
12671  Room service Family rooms 24-hour front desk D...      8.0   
12672                                  Air conditioning       6.0   
12673                                  Air conditioning       2.0   
12674  Airport shuttle Room service Non-smoking rooms...      4.0   

                                          type  
0      Deluxe Double Room (2 Adults + 1 Child)  
1      Deluxe Double Room (2 Adults + 1 Child)  
2                 Superior Double or Twin Room  
3      Deluxe Double Room (2 Adults + 1 Child)  
4                 Superior Double or Twin Room  
...                                        ...  
12670                       Deluxe Triple Room  
12671                      Classic Triple Room  
12672                     Standard Double Room  
12673                      Classic Triple Room  
12674                     Standard Double Room  

[12675 rows x 6 columns]

In [27]:
dfd=dfd.drop_duplicates(ignore_index=True)
dfd

price                 location  distance  \
0      900  Pashim Vihar, New Delhi       NaN   
1     4125     Paharganj, New Delhi       NaN   
2     1259    South West, New Delhi       NaN   
3      920    South West, New Delhi       NaN   
4     2000     Paharganj, New Delhi       NaN   
..     ...                      ...       ...   
730    489    South West, New Delhi       NaN   
731    929        Dwarka, New Delhi       NaN   
732    970                New Delhi       NaN   
733    487                New Delhi       NaN   
734    437        Rohini, New Delhi       NaN   

                                             amenities  ratings  \
0    Room service Non-smoking rooms Free WiFi Free ...      8.5   
1    Airport shuttle Room service Fitness centre No...      8.3   
2    Airport shuttle Room service Non-smoking rooms...      8.4   
3    Room service Free parking Spa and wellness cen...      7.8   
4    Airport shuttle Spa and wellness centre Room s...      8.0   
..                                                 ...      ...   
730  Room service Family rooms 24-hour front desk D...      1.0   
731                                         Free WiFi       4.6   
732  Room service Daily housekeeping Air conditioning       1.0   
733  Room service 24-hour front desk Daily housekee...      2.3   
734  Room service Non-smoking rooms Daily housekeep...      4.0   

                                        type  
0    Deluxe Double Room (2 Adults + 1 Child)  
1               Superior Double or Twin Room  
2               Superior Double or Twin Room  
3                         Deluxe Double Room  
4                       Superior Double/Twin  
..                                       ...  
730                      Classic Triple Room  
731                      Classic Triple Room  
732                      Classic Triple Room  
733                      Classic Triple Room  
734                      Classic Triple Room  

[735 rows x 6 columns]

In [20]:
dfd.drop

In [28]:
dfd.to_csv('test.csv')